In [1]:
#import packages

import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import geopandas as gpd
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore')

In [2]:
#read cvs with lat and long all Colorado wells

df_CO = pd.read_csv('./data/COGCC wells.csv') # downloaded from COGCC

# import wells Raton Geothermal Study (2009) 
df_Raton = pd.read_csv('./data/Oil_Gas_Wells_with_Predicted_Geothermal_Properties.csv')

df_CO_coreTC = pd.read_excel('./data/USGS_Thermal_Documents.xlsx')

In [3]:
df_CO.sample(5)

API  API_County  API_Seq     API_Label  Operat_Num  \
77597  12312666         123    12666  05-123-12666       47120   
32610   6306304          63     6304  05-063-06304       61250   
44303   7506539          75     6539  05-075-06539       17888   
12795   4340042          43    40042  05-043-40042       44390   
89737  12325021         123    25021  05-123-25021       90950   

                              Operator Well_Num             Well_Name  \
77597  KERR MCGEE OIL & GAS ONSHORE LP        1  MILTON H. NELSON 'K'   
32610        MULL DRILLING COMPANY INC     1-16          STATE CROUSE   
44303                    COBB-STRINGER        1                  COLE   
12795                    JAVERNICK OIL      450               JOHNSON   
89737                           UNIOIL   21-17U             ZIMMERMAN   

                   Well_Title Citing_Typ  ... Qtr_Qtr  Section  Township  \
77597  1 MILTON H. NELSON 'K'     ACTUAL  ...    NENW       29        2N   
32610       1-16 STATE CROUSE     ACTUAL  ...    S2SW       16       10S   
44303                  1 COLE     ACTUAL  ...    NENE       14        9N   
12795             450 JOHNSON     ACTUAL  ...    NWNE        4       20S   
89737        21-17U ZIMMERMAN        NaN  ...    NENW       17        5N   

       Range  Meridian   Latitude   Longitude   Utm_X    Utm_Y      api10  
77597    68W         6  40.114880 -105.029940  497449  4440508  512312666  
32610    45W         6  39.174441 -102.441449  721019  4339253  506306304  
44303    55W         6  40.759326 -103.479864  628312  4513152  507506539  
12795    69W         6  38.344750 -105.112580  490162  4244073  504340042  
89737    67W         6  40.405110 -104.919060  506868  4472725  512325021  

[5 rows x 37 columns]

In [4]:
print(df_CO.api10.values)

[500105000 500105001 500105002 ... 512560008 512560009 512560010]


## COLORADO GEOLOGICAL SURVEY
## Map Series MS-48 
### Description of Oil and Gas Wells with Predicted Geothermal Properties Database 

June 2009

HF_Range - Predicted geothermal heat flow range (mW/m2) based on well location and extracted from heat flow zones from CGS publication MS-45 Interpretive Geothermal Heat Flow Map of Colorado. See abstract or map explanation for further details.

Gradient_Range - Predicted geothermal gradient range (deg C/km) based on well location and extracted from gradient zones from CGS publication MS-51 Interpretive Geothermal Gradient Map of Colorado. See abstract or map explanation for further details.

HF_Tier - Predicted geothermal heat flow range tier ranking. 
Tiers are divided as follows: 
Tier 1 HF >150 mW/m2, 
Tier 2 HF 120-150 mW/m2, 
Tier 3 HF 90-120 mW/m2, 
Tier 4 HF <90 mW/m2

Gradient_Tier - Predicted geothermal gradient range tier ranking. 
Tiers are divided as follows: 
Tier 1 Grad >70 degC/km, 
Tier 2 Grad 60-70 degC/km, 
Tier 3 Grad 50-60 degC/km, 
Tier 4 Grad <50 degC/km


### Reference
A Preliminary Analysis of Geothermal Resources in the Central Raton Basin, Colorado, from Bottom-Hole Temperature Data. Paul Morgan

In [6]:
fig = px.scatter_mapbox(df_Raton, lat="lat", lon="long_", color='Gradient_T',
                                zoom=9, height=600, colorscale = 'Rainbow', reversescale = True,
                                hover_data={'well_name': True,
                                            'lat': False,
                                            'long_': False,
                                            'api': True,
                                            'operator': True,
                                            'sec': True,
                                            'twp': True,
                                            'range': True})

fig.update_layout(mapbox_style="open-street-map")

fig

TypeError: scatter_mapbox() got an unexpected keyword argument 'colorscale'

In [9]:
fig = px.scatter_mapbox(df_Raton, lat="lat", lon="long_", color='HF_Tier',
                                zoom=9, height=600,
                                hover_data={'well_name': True,
                                            'lat': False,
                                            'long_': False,
                                            'api': True,
                                            'operator': True,
                                            'sec': True,
                                            'twp': True,
                                            'range': True})

fig.update_layout(mapbox_style="open-street-map")

fig

In [36]:
#Extract all wells Raton Basin

twp_list = ['31S', '32S', '33S', '34S', '35S']
range_list = ['61W', '62W', '63W', '64W', '65W', '66W', '67W', '68W']
temp = df_CO[df_CO['Township'].isin(twp_list)] 
df_Raton_CO = temp[temp['Range'].isin(range_list)] 
len(df_Raton_CO)

3881

In [37]:
df_Raton_CO['Spud_Date'] = df_Raton_CO['Spud_Date'].fillna('0000-00-00')
df_Raton_CO = df_Raton_CO.join(df_Raton_CO['Spud_Date'].str.split('-', expand=True).add_prefix('date'))
df_obj = df_Raton_CO.select_dtypes(['object'])
df_Raton_CO[df_obj.columns] = df_obj.apply(lambda x: x.str.strip())
df_Raton_CO['date0'] = df_Raton_CO['date0'].astype(int)

In [38]:
df_Raton_CO_2009 = df_Raton_CO[(df_Raton_CO['date0'] >= 2009)]
len(df_Raton_CO_2009)

99

In [43]:
df_Raton_CO_2009[['api10','date0', 'Spud_Date', 'Max_TVD', 'Max_MD', 'Operator', 
                  'Well_Name', 'Township', 'Range','Section']] 

api10  date0   Spud_Date  Max_TVD  Max_MD  \
40091  507108031   2011  2011-09-29      NaN  2570.0   
40928  507108870   2009  2009-09-22   2015.0  2015.0   
41149  507109091   2011  2011-01-12      NaN  2776.0   
41327  507109269   2011  2011-07-09      NaN  2484.0   
41396  507109338   2011  2011-10-10      NaN  1965.0   
...          ...    ...         ...      ...     ...   
41934  507109879   2011  2011-07-20      NaN  2566.0   
41940  507109885   2011  2011-10-25      NaN  2565.0   
41953  507109898   2011  2011-11-28      NaN  1850.0   
41966  507109911   2012  2012-05-28      NaN  1742.0   
41971  507109916   2014  2014-04-15      NaN  7215.0   

                              Operator         Well_Name Township Range  \
40091  EVERGREEN NATURAL RESOURCES LLC         Petrogulf      33S   67W   
40928  EVERGREEN NATURAL RESOURCES LLC  North Fork Ranch      33S   68W   
41149  EVERGREEN NATURAL RESOURCES LLC              Wood      33S   68W   
41327  EVERGREEN NATURAL RESOURCES LLC            Barrow      32S   66W   
41396  EVERGREEN NATURAL RESOURCES LLC           VALLEJO      33S   67W   
...                                ...               ...      ...   ...   
41934       TIMBER CREEK OPERATING LLC     APACHE CANYON      34S   67W   
41940  EVERGREEN NATURAL RESOURCES LLC            Hunter      33S   67W   
41953  EVERGREEN NATURAL RESOURCES LLC          Champion      33S   66W   
41966       NATURAL RESOURCE GROUP INC             Largo      34S   62W   
41971  EVERGREEN NATURAL RESOURCES LLC         San Pablo      33S   67W   

       Section  
40091        9  
40928        1  
41149        2  
41327        8  
41396       19  
...        ...  
41934       30  
41940       17  
41953        9  
41966        4  
41971        4  

[99 rows x 10 columns]

In [44]:
df_Raton_CO_2009_3200 = df_Raton_CO_2009[(df_Raton_CO_2009['Max_MD'] >= 3200)]
df_Raton_CO_2009_3200[['api10','date0', 'Spud_Date', 'Max_TVD', 'Max_MD', 'Operator', 
                  'Well_Name', 'Township', 'Range','Section']]

api10  date0   Spud_Date  Max_TVD  Max_MD  \
41754  507109697   2009  2009-11-28   3240.0  3240.0   
41771  507109714   2011  2011-06-27      NaN  3314.0   
41790  507109733   2009  2009-09-28      NaN  6601.0   
41893  507109838   2011  2011-01-08      NaN  6610.0   
41971  507109916   2014  2014-04-15      NaN  7215.0   

                              Operator         Well_Name Township Range  \
41754  EVERGREEN NATURAL RESOURCES LLC            Redbud      32S   66W   
41771  EVERGREEN NATURAL RESOURCES LLC             CEDAR      32S   67W   
41790       TIMBER CREEK OPERATING LLC  LOPEZ CANYON SWD      33S   67W   
41893             WAPITI OPERATING LLC             VPR C      35S   67W   
41971  EVERGREEN NATURAL RESOURCES LLC         San Pablo      33S   67W   

       Section  
41754        7  
41771       19  
41790       21  
41893        1  
41971        4

In [66]:
fig = go.Figure()

fig.add_trace(go.Scattermapbox(
        lat=df_Raton_CO.Latitude,
        lon=df_Raton_CO.Longitude,
        name ='Raton Basin Wells (2009)',
        mode='markers',
        marker=go.scattermapbox.Marker(size=5,color='rgb(255, 0, 0)',opacity=0.5),
        text=df_CO.Well_Name,hoverinfo='none'))

fig.add_trace(go.Scattermapbox(
        lat=df_Raton_CO_2009.Latitude,
        lon=df_Raton_CO_2009.Longitude,
        name ='Raton Basin Wells (>2009)',
        mode='markers',
        marker=go.scattermapbox.Marker(size=4,color='rgb(0, 255, 0)',opacity=0.7),
        text=df_Raton_CO_2009.Well_Name,hoverinfo='text'))

fig.add_trace(go.Scattermapbox(
        lat=df_CO_coreTC.latitude,
        lon=df_CO_coreTC.longitude,
        name ='USGS Core Thermal Conductivity',
        mode='markers',
        marker=go.scattermapbox.Marker(size=5,color='rgb(0, 0, 255)',opacity=0.7),
        hoverinfo='none'))

fig.update_layout(mapbox_style="open-street-map")

fig.update_layout(
    title='Raton Basin Wells',
    autosize=True,
    hovermode='closest',
    showlegend=True, mapbox=dict(center=dict(lat=37,lon=-104)))

fig.show()

In [2]:
#Extract Temperature curves and/or BHT from 2009 wells and newer wells

#find LAS files

#option 1 to get from a csv file 

LAS_files=pd.read_csv('./data/Las available.csv')


In [4]:
LAS_files['DocUrl'].head(5)

0    http://ogccweblink.state.co.us/DownloadDocumen...
1    http://ogccweblink.state.co.us/DownloadDocumen...
2    http://ogccweblink.state.co.us/DownloadDocumen...
3    http://ogccweblink.state.co.us/DownloadDocumen...
4    http://ogccweblink.state.co.us/DownloadDocumen...
Name: DocUrl, dtype: object

In [85]:
#USING Scraping data -- (MB Mines) example 1 well
import requests
baseURL = 'https://cogcc.state.co.us/cogis/FacilityDetail.asp?facid='
tailURL = '&type=WELL'
#url = baseURL + '05-057-05128'.replace('-','')[2:] + tailURL
url = baseURL + '07109733' + tailURL
print('URL:', url)
r = requests.get(url)
print('Encoding:', r.encoding)
print('RespCode:',type(r.status_code),r.status_code)

URL: https://cogcc.state.co.us/cogis/FacilityDetail.asp?facid=07109733&type=WELL
Encoding: ISO-8859-1
RespCode: <class 'int'> 200


In [86]:
r.text

'\r\n  \r\n<html>\r\n\r\n<head>\r\n\r\n\r\n\r\n\t<title>COGIS - WELL Information</title>\r\n</head>\r\n\r\n<body onLoad=window.focus()>\r\n\r\n\r\n<font face="Arial" size="2">\r\n<!--\r\n<img SRC="images/s_cogcc_head.jpg" width="513" height="51" alt="Colorado Oil & Gas Conservation Commission"><br>\r\n<img SRC="images/s_head_fill.jpg" width="123" height="22">\r\n -->\r\n\r\n<p><font size="5" color="#000080" face="Arial"><b>&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;\r\n COGIS - WELL Information</b></font></p>\r\n\r\n\r\n\r\n\r\n\t\t\r\n\t\t<!-- BEGIN OUTPUT TO SCREEN -->\r\n\t\t<!-- BEGIN SURFACE INFORMATION -->\r\n\t\t\r\n\t\t<!-- HANDLE BAD API NUMBER -->\r\n\t\t\r\n\r\n\t\t<table cellspacing="1" cellpadding="1" border="0">\r\n\t\t\t<tr>\r\n\t\t\t\t<td colspan="4" bgcolor="#ffffcc">\r\n\t\t\t\t\t\t<font size="2">\r\n\t\t\t\t<table>\r\n\t\t\t\t<tr>\r\n\t\t\t\t\r\n\t\t\t\t\r\n\t\t\r\n\t\t\t\t<td valign="top"><font size="4" color="Navy">Scout Card</font>&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbs

In [87]:
def top_parse(text):
    tops = text.split('<!-- LOOP FOR EACH Formation WITHIN WELLBORE -->')[1].split('<!-- END Formation LOOP -->')[0]
    tops = tops.replace('\r','').replace('\n','').replace('\t','').strip()
    tops = tops.split('<tr>')
    tops = [x.strip() for x in tops if len(x) > 0]
    
    formations = {}
    for top in tops:
        cols = top.split('<td')
        cols = [x.strip() for x in cols if len(x) > 0]    
        formation = cols[0].split('color="Navy">')[1].split(' ')[0]
        depth = eval(cols[1].split('<font size="2">')[1].split('</font>')[0])
        formations[formation] = depth
    return formations

In [88]:
top_parse(r.text)

{'VERMEJO': 1546, 'TRINIDAD': 1840, 'PIERRE': 2054}